# WebScrapping the data

In order to obtain the data for my project, I decided to scrap it from the internet.

I started doing some scrapping from Netflix, but I couldn't obtain all the information that I wanted; that's when I decided to do it from FilmAffinity, a web page for vote and recommending movies and TV shows. From here I could get information like the year of release, the country of release, the directors, the cast or the reviews for each one.

I managed to scrap around one thousand samples from FilmAffinity, but I found some differences between this data and the one scrapped from Netflix; so I decided to merge both datasets and scrap everything again, in order to obtain more information.

The last step is what you can find in this notebook.

In [1]:
import numpy as np
import pandas as pd
import time

import requests
from bs4 import BeautifulSoup

### Reading the complete dataset

I started reading the complete dataset, that contains all the links from FilmAffinity, the ones that I will use to get the information from each movie and TV show.

Next, I did some data cleaning, deleting duplicates and selecting the important columns.

In [2]:
data = pd.read_csv('datasets/netflix_2.csv', index_col=0, sep=';')
data.head()

Title                                             Link    Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  series   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  series   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  series   
4    Prison Break  https://www.filmaffinity.com/us/film822756.html  series   
5  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  series   

   Year_Release Duration Country Directors Cast Genres Description  \
0           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
1           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
2           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
4           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
5           NaN      NaN     NaN       NaN  NaN    NaN         NaN   

   RatingAverage  Votes Reviews  
0            NaN    NaN     NaN  
1            NaN    NaN     NaN  
2            NaN    NaN     NaN  
4            NaN    NaN     NaN  
5            NaN    NaN     NaN

In [3]:
data['Link'].duplicated().sum()

95

In [4]:
data = data.drop_duplicates(subset='Link')
data.head()

Title                                             Link    Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  series   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  series   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  series   
4    Prison Break  https://www.filmaffinity.com/us/film822756.html  series   
5  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  series   

   Year_Release Duration Country Directors Cast Genres Description  \
0           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
1           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
2           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
4           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
5           NaN      NaN     NaN       NaN  NaN    NaN         NaN   

   RatingAverage  Votes Reviews  
0            NaN    NaN     NaN  
1            NaN    NaN     NaN  
2            NaN    NaN     NaN  
4            NaN    NaN     NaN  
5            NaN    NaN     NaN

In [5]:
data['Link'].duplicated().sum()

0

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2383 entries, 0 to 2565
Data columns (total 13 columns):
 #   Column         Non-Null Count  Dtype  
---  ------         --------------  -----  
 0   Title          2383 non-null   object 
 1   Link           2383 non-null   object 
 2   Type           2383 non-null   object 
 3   Year_Release   1238 non-null   float64
 4   Duration       1167 non-null   object 
 5   Country        1238 non-null   object 
 6   Directors      1221 non-null   object 
 7   Cast           1237 non-null   object 
 8   Genres         1238 non-null   object 
 9   Description    1061 non-null   object 
 10  RatingAverage  1104 non-null   float64
 11  Votes          1104 non-null   float64
 12  Reviews        1033 non-null   object 
dtypes: float64(3), object(10)
memory usage: 260.6+ KB


In [7]:
data = data.reset_index(drop=True)
data.head()

Title                                             Link    Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  series   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  series   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  series   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  series   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  series   

   Year_Release Duration Country Directors Cast Genres Description  \
0           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
1           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
2           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
3           NaN      NaN     NaN       NaN  NaN    NaN         NaN   
4           NaN      NaN     NaN       NaN  NaN    NaN         NaN   

   RatingAverage  Votes Reviews  
0            NaN    NaN     NaN  
1            NaN    NaN     NaN  
2            NaN    NaN     NaN  
3            NaN    NaN     NaN  
4            NaN    NaN     NaN

In [8]:
data.Type.value_counts()

film      1371
series     534
serie      478
Name: Type, dtype: int64

In [9]:
type_dict = {'series':'TV show', 'serie':'TV show'}

In [10]:
data['Type'].replace(type_dict, inplace=True)
data.Type.value_counts()

film       1371
TV show    1012
Name: Type, dtype: int64

In [11]:
data.columns

Index(['Title', 'Link', 'Type', 'Year_Release', 'Duration', 'Country',
       'Directors', 'Cast', 'Genres', 'Description', 'RatingAverage', 'Votes',
       'Reviews'],
      dtype='object')

In [12]:
df = data[['Title', 'Link', 'Type']]
df.head()

Title                                             Link     Type
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show

In [13]:
len(df)

2383

### Scrapping the data

From here, I started doing the web scrapping. As FilmAffinity uses captcha to detect if there's a bot obtaining the information, I printed the movie link and the response from the page, in order to check if this captcha is being activated. If so, I went to FilmAffinity and verified manually the captcha, so my running code could continue scrapping the information.

In a second round, I checked all the missing values (NaN) and scrapped the information again.

#### Scrapping the year of release

In [3]:
yearRelease = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # year of release
    print(soupFilm.find('dd', itemprop='datePublished'))
    print(soupFilm.find('dd', itemprop='datePublished') == None, '\n')
    
    if (soupFilm.find('dd', itemprop='datePublished')) != None:
        yearRelease.append(soupFilm.find('dd', itemprop='datePublished').string)
    else:
        yearRelease.append('NaN')

https://www.filmaffinity.com/us/film879405.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film573633.html
<dd itemprop="datePublished">2013</dd>
False 

https://www.filmaffinity.com/us/film441483.html
<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/us/film822756.html
<dd itemprop="datePublished">2005</dd>
False 

https://www.filmaffinity.com/us/film999360.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film103430.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film910593.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film482516.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film539830.html
<dd itemprop="datePublished">2013</dd>
False 

https://www.filmaffinity.com/us/film340588.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film512020.html
<d

<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/us/film460960.html
<dd itemprop="datePublished">2005</dd>
False 

https://www.filmaffinity.com/us/film292512.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film225440.html
<dd itemprop="datePublished">1990</dd>
False 

https://www.filmaffinity.com/us/film846678.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film847347.html
<dd itemprop="datePublished">2013</dd>
False 

https://www.filmaffinity.com/us/film658214.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film900221.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film129408.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film447173.html
<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/us/film233858.html
<dd itemprop="datePublished">2013</dd>
False 

htt

<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film385033.html
<dd itemprop="datePublished">2003</dd>
False 

https://www.filmaffinity.com/us/film976071.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film132399.html
<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/us/film206694.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film575941.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film341150.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film507956.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film107452.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film938902.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film971429.html
<dd itemprop="datePublished">2017</dd>
False 

htt

<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/us/film280010.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/us/film907965.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/us/film296760.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film842043.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film315112.html
<dd itemprop="datePublished">2013</dd>
False 

https://www.filmaffinity.com/us/film515579.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film698732.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film942291.html
<dd itemprop="datePublished">2010</dd>
False 

https://www.filmaffinity.com/us/film884519.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film585746.html
<dd itemprop="datePublished">2019</dd>
False 

htt

False 

https://www.filmaffinity.com/us/film674963.html
<dd itemprop="datePublished">2010</dd>
False 

https://www.filmaffinity.com/us/film812149.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/us/film661739.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film948280.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/us/film294756.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film951448.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/us/film409270.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/us/film379997.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film920710.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/us/film156800.html
<dd itemprop="datePublished">2012</dd>
False 

https://www.filmaffinity.com/us/film177390

...

<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/es/film528779.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film346271.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film319251.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/es/film480290.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/es/film288287.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film986529.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film882518.html
<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/es/film764527.html
<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/es/film277060.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film426853.html
<dd itemprop="datePublished">2017</dd>
False 

htt

<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film452096.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film137726.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/es/film139847.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film585032.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film307683.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film646268.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/es/film540071.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film511574.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film648435.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film215051.html
<dd itemprop="datePublished">2019</dd>
False 

htt

<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film338166.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film667556.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film553614.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film676619.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film768004.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film746466.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film767847.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film885451.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film335668.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/es/film586794.html
<dd itemprop="datePublished">2019</dd>
False 

htt

<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film726898.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/es/film747300.html
<dd itemprop="datePublished">2013</dd>
False 

https://www.filmaffinity.com/es/film454034.html
<dd itemprop="datePublished">2014</dd>
False 

https://www.filmaffinity.com/es/film734762.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film343554.html
<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/es/film280367.html
<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/es/film305160.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/es/film837340.html
<dd itemprop="datePublished">2017</dd>
False 

https://www.filmaffinity.com/es/film119391.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film916911.html
<dd itemprop="datePublished">2017</dd>
False 

htt

<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film274644.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film177387.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film211384.html
<dd itemprop="datePublished">2018</dd>
False 

https://www.filmaffinity.com/es/film251062.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film644211.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film294683.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film103261.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film508974.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film758486.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film261685.html
<dd itemprop="datePublished">2019</dd>
False 

htt

In [4]:
len(yearRelease)

2383

In [6]:
df['Year_Release'] = yearRelease
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  RatingAverage  ...  \
0  TV Series (2017-Present Day). 4 Seasons. A mys...            7.1  ...   
1  The world's most wanted criminal, Thomas Raymo...            6.4  ...   
2  Macarena Ferreiro is a young naive woman who f...            7.0  ...   
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....            7.3  ...   
4  'Thirteen Reasons Why', based on the best-sell...            6.8  ...   

                                             Reviews Women_Cast  Men_Cast  \
0  "[4th Season Review]: [It] is like an extended...         11        26   
1  "His name is above the title and, depending ho...          9        15   
2                                                NaN         21         9   
3  "A strong cast led by Wentworth Miller (...) I...          4        15   
4  "[2nd Season Review]: [It] is a frustratingly ...         12        22   

   Not_Set_Cast  Total_Cast  Women_Directors  Men_Directors  \
0             2          39                0              5   
1             0          24                4             32   
2             2          32                2              3   
3             2          21                1             30   
4             1          35                2              5   

   Not_Set_Directors  Total_Directors  Year_Release  
0                  2                7          2017  
1                  0               36          2013  
2                  4                9          2015  
3                  1               32          2005  
4                  0                7          2017  

[5 rows x 21 columns]

In [10]:
# Repeat the process in order to get the information from NaN values
for item in df.index:
    print(df.Link[item])
    if (df.Year_Release[item]) == 'NaN':
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # year of release
        print(soupFilm.find('dd', itemprop='datePublished'))
        print(soupFilm.find('dd', itemprop='datePublished') == None, '\n')
    
        if (soupFilm.find('dd', itemprop='datePublished')) != None:
            df.Year_Release[item] = soupFilm.find('dd', itemprop='datePublished').string
        else:
            df.Year_Release[item] = 'NaN'

https://www.filmaffinity.com/us/film879405.html
https://www.filmaffinity.com/us/film573633.html
https://www.filmaffinity.com/us/film441483.html
https://www.filmaffinity.com/us/film822756.html
https://www.filmaffinity.com/us/film999360.html
https://www.filmaffinity.com/us/film103430.html
https://www.filmaffinity.com/us/film910593.html
https://www.filmaffinity.com/us/film482516.html
https://www.filmaffinity.com/us/film539830.html
https://www.filmaffinity.com/us/film340588.html
https://www.filmaffinity.com/us/film512020.html
https://www.filmaffinity.com/us/film654725.html
https://www.filmaffinity.com/us/film187456.html
https://www.filmaffinity.com/us/film489970.html
https://www.filmaffinity.com/us/film966117.html
https://www.filmaffinity.com/us/film718452.html
https://www.filmaffinity.com/us/film194842.html
https://www.filmaffinity.com/us/film880530.html
https://www.filmaffinity.com/us/film828822.html
https://www.filmaffinity.com/us/film668282.html
https://www.filmaffinity.com/us/film9402

<dd itemprop="datePublished">2015</dd>
False 

https://www.filmaffinity.com/us/film562428.html


/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  del sys.path[0]


<dd itemprop="datePublished">2010</dd>
False 

https://www.filmaffinity.com/us/film567879.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/us/film171299.html
<dd itemprop="datePublished">2008</dd>
False 

https://www.filmaffinity.com/us/film104238.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/us/film660520.html
<dd itemprop="datePublished">1993</dd>
False 

https://www.filmaffinity.com/es/film410388.html
<dd itemprop="datePublished">2016</dd>
False 

https://www.filmaffinity.com/es/film722036.html
<dd itemprop="datePublished">2020</dd>
False 

https://www.filmaffinity.com/ca/film839631.html
<dd itemprop="datePublished">2019</dd>
False 

https://www.filmaffinity.com/es/film952832.html
<dd itemprop="datePublished">2010</dd>
False 

https://www.filmaffinity.com/us/film101875.html
<dd itemprop="datePublished">2012</dd>
False 

https://www.filmaffinity.com/us/film716669.html
<dd itemprop="datePublished">1961</dd>
False 

htt

In [11]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

In [4]:
df = pd.read_csv('datasets/filmaffinity_data2.csv', index_col=0)
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...  
1  James Spader, Megan Boone, Diego Klattenhoff, ...  
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...  
3  Wentworth Miller, Dominic Purcell, Robert Knep...  
4  Dylan Minnette, Katherine Langford, Christian ...

#### Scrapping the duration

In [ ]:
duration = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # duration
    print(soupFilm.find('dd', itemprop='duration'))
    print(soupFilm.find('dd', itemprop='duration') == None, '\n')
    
    if (soupFilm.find('dd', itemprop='duration')) != None:
        duration.append(soupFilm.find('dd', itemprop='duration').string)
    else:
        duration.append('NaN')

In [ ]:
len(duration)

In [ ]:
df['Duration'] = duration
df.head()

In [ ]:
# Repeat the process in order to get the information from NaN values
for item in df.index:
    if (df.Duration[item]) == 'NaN':
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # duration
        print(soupFilm.find('dd', itemprop='duration'))
        print(soupFilm.find('dd', itemprop='duration') == None, '\n')
    
        if (soupFilm.find('dd', itemprop='duration')) != None:
            df.Duration[item] = soupFilm.find('dd', itemprop='duration').string
        else:
            df.Duration[item] = 'NaN'

In [ ]:
df.head()

In [ ]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the country of release

In [ ]:
country = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # country
    print(soupFilm.find('span', id ='country-img'))
    print((soupFilm.find('span', id ='country-img')) == None, '\n')
    
    if ((soupFilm.find('span', id ='country-img')) != None):
        country.append(soupFilm.find('span', id ='country-img').find('img').get('title'))
    else:
        country.append('NaN')

In [ ]:
len(country)

In [ ]:
df['Country'] = country
df.head()

In [ ]:
# Repeat the process in order to get the information from NaN values
for item in df.index:
    if (df.Country[item]) == 'NaN':
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # country
        print(soupFilm.find('span', id ='country-img'))
        print((soupFilm.find('span', id ='country-img')) == None, '\n')
    
        if (soupFilm.find('span', id ='country-img')) != None:
            df.Country[item] = soupFilm.find('span', id ='country-img').find('img').get('title')
        else:
            df.Country[item] = 'NaN'

In [ ]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the directors

In [ ]:
directors = []
directorsComplete = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # directors
    print(soupFilm.find_all('span', itemprop='director'))
    print((soupFilm.find_all('span', itemprop='director'))==None, '\n')
    
    for director in soupFilm.find_all('span', itemprop='director'):
        directors.append(director.find('span', itemprop='name').string)
    
    directorsComplete.append(directors)
    directors = []

In [ ]:
len(directorsComplete)

In [ ]:
df['Directors'] = [', '.join(director) for director in directorsComplete]
df.head()

In [ ]:
# Repeat the process in order to get the information from NaN values
directors2 = []

for item in df.index:
    if len((df.Directors[item])) == 0:
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
    
        # directors
        print(soupFilm.find_all('span', itemprop='director'))
        print((soupFilm.find_all('span', itemprop='director'))==None, '\n')
    
        for director in soupFilm.find_all('span', itemprop='director'):
            directors2.append(director.find('span', itemprop='name').string)
    
        df.Directors[item] = ', '.join(directors2)
        directors2 = []

In [ ]:
df.head()

In [ ]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the cast

In [ ]:
cast = []
castComplete = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # cast
    print(soupFilm.find_all('span', itemprop='actor'))
    print((soupFilm.find_all('span', itemprop='actor')) == None, '\n')
    
    for actor in soupFilm.find_all('span', itemprop='actor'):
        cast.append(actor.find('span', itemprop='name').string)
    
    castComplete.append(cast)
    cast = []

In [ ]:
len(castComplete)

In [ ]:
df['Cast'] = [', '.join(cast) for cast in castComplete]
df.head()

In [ ]:
# Repeat the process in order to get the information from NaN values
cast2 = []

for item in df.index:
    if len((df.Cast[item])) == 0:
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
    
        # cast
        print(soupFilm.find_all('span', itemprop='actor'))
        print((soupFilm.find_all('span', itemprop='actor')) == None, '\n')
    
        for actor in soupFilm.find_all('span', itemprop='actor'):
            cast2.append(actor.find('span', itemprop='name').string)
    
        df.Cast[item] = ', '.join(cast2)
        cast2 = []

In [ ]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the cinematographic genres

In [6]:
genres = []
genresComplete = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # genres
    print(soupFilm.find_all('dd', 'card-genres'))
    print((soupFilm.find_all('dd', 'card-genres')) == None, '\n')
    
    item = soupFilm.find_all('dd', 'card-genres')
    if len(item) != 0:
        for genre in item[0].find_all('a'):
            genres.append(genre.text)
    else:
        genres.append('NaN')
    
    genresComplete.append(genres)
    genres = []

https://www.filmaffinity.com/us/film879405.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TH&amp;attr=rat_count&amp;nodoc">Thriller</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=INT&amp;attr=rat_count&amp;nodoc">Mystery</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=938448&amp;attr=rat_count&amp;nodoc">Heist Film</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=156542&amp;attr=rat_count&amp;nodoc">Kidnapping Film / Disappearance</a> </dd>]
False 

https://www.filmaffinity.com/us/film573633.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=r

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DO&amp;attr=rat_count&amp;nodoc">Documentary</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=676077&amp;attr=rat_count&amp;nodoc">TV Miniseries</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=206211&amp;attr=rat_count&amp;nodoc">Based On A True Story</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=345640&amp;attr=rat_count&amp;nodoc">Biography</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=836459&amp;attr=rat_count&amp;nodoc">Sexual Abuse</a> </dd>]
False 

https://www.filmaffinity.com/us/film654725.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.f

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=AC&amp;attr=rat_count&amp;nodoc">Action</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=RO&amp;attr=rat_count&amp;nodoc">Romance</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=534658&amp;attr=rat_count&amp;nodoc">Telenovela / Latino Soap Opera</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=959297&amp;attr=rat_count&amp;nodoc">Mafia</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=509612&amp;attr=

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=AC&amp;attr=rat_count&amp;nodoc">Action</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TH&amp;attr=rat_count&amp;nodoc">Thriller</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=524594&amp;attr=rat_count&amp;nodoc">Crime</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=509612&amp;attr=rat_count&amp;nodoc">Drugs</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=197567&amp;attr=rat_count&amp;nodoc">Rem

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TH&amp;attr=rat_count&amp;nodoc">Thriller</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=213643&amp;attr=rat_count&amp;nodoc">Politics</a> </dd>]
False 

https://www.filmaffinity.com/us/film482651.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=AC&amp;attr=rat_count&amp;nodoc">Action</a></span>.           

...

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=C-F&amp;attr=rat_count&amp;nodoc">Ciencia ficción</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=FAN&amp;attr=rat_count&amp;nodoc">Fantástico</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=574004&amp;attr=rat_count&amp;nodoc">Telefilm</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=180914&amp;attr=rat_count&amp;nodoc">Mediometraje</a> </dd>]
False 

https://www.filmaffinity.com/es/film767770.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=FAN&amp;attr=rat_count&amp;nodoc">Fantástico</a></span>.                 <span it

https://www.filmaffinity.com/es/film248229.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=rat_count&amp;nodoc">Comedia</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=630442&amp;attr=rat_count&amp;nodoc">Música</a> </dd>]
False 

https://www.filmaffinity.com/es/film683886.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=r

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=rat_count&amp;nodoc">Comedia</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=279137&amp;attr=rat_count&amp;nodoc">Familia</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=708976&amp;attr=rat_count&amp;nodoc">Adopción</a> </dd>]
False 

https://www.filmaffinity.com/es/film885341.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DO&amp;attr=rat_count&amp;nodoc">Documental</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span> </dd>]
False 

https://www.f

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TE&amp;attr=rat_count&amp;nodoc">Terror</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=865591&amp;attr=rat_count&amp;nodoc">Sobrenatural</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=636348&amp;attr=rat_count&amp;nodoc">Aventuras marinas</a> </dd>]
False 

https://www.filmaffinity.com/es/film279204.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AV&amp;attr=rat_count&amp;nodoc">Aventuras</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=694593&amp;attr=rat_count&amp;nodoc">Prehistoria</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=784111&amp;attr=rat_count&amp;nodoc">Supervivencia</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.ph

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=rat_count&amp;nodoc">Comedia</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=213643&amp;attr=rat_count&amp;nodoc">Política</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=333692&amp;attr=rat_count&amp;nodoc">Sátira</a> </dd>]
False 



In [7]:
len(genresComplete)

2383

In [8]:
df['Genres'] = [', '.join(genre) for genre in genresComplete]
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  
0  TV Series, Thriller, Mystery, Heist Film, Kidn...  
1         TV Series, Mystery, Drama, Crime, Spy Film  
2           TV Series, Thriller, Drama, Prison Drama  
3  TV Series, Action, Drama, Prison Drama, Cop Mo...  
4  TV Series, Drama, Mystery, Teen/coming-of-age,...

In [9]:
# Repeat the process in order to get the information from NaN values
genres2 = []

for item in df.index:
    if df.Genres[item] == 'NaN':
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
    
        # genres
        print(soupFilm.find_all('dd', 'card-genres'))
        print((soupFilm.find_all('dd', 'card-genres')) == None, '\n')
        
        i = soupFilm.find_all('dd', 'card-genres')
        if len(i) != 0:
            for genre in i[0].find_all('a'):
                genres2.append(genre.text)
        else:
            genres2.append('NaN')
    
        df.Genres[item] = ', '.join(genres2)
        genres2 = []

https://www.filmaffinity.com/us/film402563.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=449883&amp;attr=rat_count&amp;nodoc">Dancing</a> </dd>]
False 

https://www.filmaffinity.com/us/film369843.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=RO&amp;attr=rat_co

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=INT&amp;attr=rat_count&amp;nodoc">Mystery</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=524594&amp;attr=rat_count&amp;nodoc">Crime</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=954549&amp;attr=rat_count&amp;nodoc">Schools &amp; University</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=746104&amp;attr=rat_count&amp;nodoc">Teen/coming-of-age</a> </dd>]
False 

https://www.filmaffinity.com/us/film951448.html
[<dd class="card-genres">
<span itemprop="genre"><a

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=INT&amp;attr=rat_count&amp;nodoc">Mystery</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=C-F&amp;attr=rat_count&amp;nodoc">Sci-Fi</a></span> |                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=865591&amp;attr=rat_count&amp;nodoc">Supernatural</a>.                 <a href="https://www.filmaffinity.com/us/movietopic.php?topic=927100&amp;attr=rat_count&amp;nodoc">Voodoo</a> </dd>]
False 

https://www.filmaffinity.com/us/film812084.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=C-F&amp;attr=rat_count&amp;nodoc">Ciencia ficción</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TH&amp;attr=rat_count&amp;nodoc">Thriller</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=252437&amp;attr=rat_count&amp;nodoc">Aviones</a> </dd>]
False 

https://www.filmaffinity.com/es/film488941.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">TV Series</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=AN&amp;attr=rat_count&amp;nodoc">Animation</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/us/moviegenre.php?genre=INF&amp;attr=rat_count&amp;nodoc">Kids</a></span> </dd>]
False 

https://www.filmaffinity.com/es/film472532.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AN&amp;attr=rat_count&amp;nodoc">Animación</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AV&amp;attr=rat_count&amp;nodoc">

...

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=INT&amp;attr=rat_count&amp;nodoc">Intriga</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=315711&amp;attr=rat_count&amp;nodoc">Internet / Informática</a> </dd>]
False 

https://www.filmaffinity.com/es/film837340.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DR&amp;attr=rat_count&amp;nodoc">Drama</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=RO&amp;attr=rat_count&amp;nodoc">Romance</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=791958&amp;attr=rat_count&amp;nodoc">Acoso escolar</a>.                 <

https://www.filmaffinity.com/es/film373704.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AN&amp;attr=rat_count&amp;nodoc">Animación</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=rat_count&amp;nodoc">Comedia</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AC&amp;attr=rat_count&amp;nodoc">Acción</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AV&amp;attr=rat_count&amp;nodoc">Aventuras</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=458310&amp;attr=rat_count&amp;nodoc">Artes marciales</a> </dd>]
False 

https://www

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AN&amp;attr=rat_count&amp;nodoc">Animación</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=295727&amp;attr=rat_count&amp;nodoc">Pixar</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=251997&amp;attr=rat_count&amp;nodoc">Cortometraje (animación)</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=407014&amp;attr=rat_count&amp;nodoc">Discapacidad</a> </dd>]
False 

https://www.filmaffinity.com/es/film121652.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AN&amp;attr=rat_count&amp;nodoc">Animación</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=CO&amp;attr=rat_count&amp;nodoc">Comedia</a></span> |                 <a href="https://www.filmaffin

False 

https://www.filmaffinity.com/es/film264485.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=FAN&amp;attr=rat_count&amp;nodoc">Fantástico</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=638971&amp;attr=rat_count&amp;nodoc">Secuela</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=574004&amp;attr=rat_count&amp;nodoc">Telefilm</a> </dd>]
False 

https://www.filmaffinity.com/es/film409143.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=TV_SE&amp;attr=rat_count&amp;nodoc">Serie de TV</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DO&amp;attr=rat_count&amp;nodoc">Documental</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=877262&amp;attr=rat_count&amp;nodoc">Documental s

[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DO&amp;attr=rat_count&amp;nodoc">Documental</a></span>.                 <span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=AV&amp;attr=rat_count&amp;nodoc">Aventuras</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=734714&amp;attr=rat_count&amp;nodoc">Animales</a>.                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=618874&amp;attr=rat_count&amp;nodoc">Naturaleza</a> </dd>]
False 

https://www.filmaffinity.com/es/film608278.html
[<dd class="card-genres">
<span itemprop="genre"><a href="https://www.filmaffinity.com/es/moviegenre.php?genre=DO&amp;attr=rat_count&amp;nodoc">Documental</a></span> |                 <a href="https://www.filmaffinity.com/es/movietopic.php?topic=760042&amp;attr=rat_count&amp;nodoc">Documental marino</a>.                 <a href="https://www.filmaffinit

In [10]:
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  
0  TV Series, Thriller, Mystery, Heist Film, Kidn...  
1         TV Series, Mystery, Drama, Crime, Spy Film  
2           TV Series, Thriller, Drama, Prison Drama  
3  TV Series, Action, Drama, Prison Drama, Cop Mo...  
4  TV Series, Drama, Mystery, Teen/coming-of-age,...

In [11]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the description

In [13]:
description = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # description
    print(soupFilm.find('dd', itemprop='description'))
    print((soupFilm.find('dd', itemprop='description')) == None, '\n')
    
    if (soupFilm.find('dd', itemprop='description')) != None:
        description.append(soupFilm.find('dd', itemprop='description').string)
    else:
        description.append('NaN')

https://www.filmaffinity.com/us/film879405.html
<dd class="" itemprop="description">TV Series (2017-Present Day). 4 Seasons. A mysterious character called the Professor is planning the biggest robbery in history. To do this, he recruits eight thieves who take hostages and lock themselves in the Royal Mint of Spain as The Professor manipulates the police to carry out his plan from the outside. This group of very peculiar robbers have a plan: assault the Factory of Moneda and Timbre to carry out the most perfect robbery in the history of Spain and taking home 2,400 million euros.<br/>
<br/>
Release date Season 4: april 2020.</dd>
False 

https://www.filmaffinity.com/us/film573633.html
<dd class="" itemprop="description">The world's most wanted criminal, Thomas Raymond Reddington (James Spader) mysteriously turns himself in and offers to give up everyone he has ever worked with. His only condition: He will only work with a newly minted FBI agent Elisabeth Keen (Megan Boone) with whom he a

None
True 

https://www.filmaffinity.com/us/film940262.html
<dd class="" itemprop="description">"Arrow" revolves around the hooded superhero, a wealthy playboy by day who secretly saves the city by night using his enhanced arrows. Oliver Queen was a spoiled, thrill-seeking playboy, until he was left stranded on a deserted island for three years. There, he trained to become a master archer in order to survive. Returning home to Seattle, he used his skills to become the costumed vigilante called Green Arrow to dispense justice. He is also well known for his left-leaning political views.</dd>
False 

https://www.filmaffinity.com/us/film243382.html
<dd class="" itemprop="description">TV Series (2017-Present Day). 3 Seasons. 30 Episodes. Marty Byrde (Jason Bateman) is a financial planner and family man who suddenly relocates from a Chicago suburb to a summer resort community in the Missouri Ozarks, and who must pay off a debt to a Mexican drug lord.</dd>
False 

https://www.filmaffinity.com

<dd class="" itemprop="description">TV Series (2017-Present Day). Year 1977. An agent in the FBI's Elite Serial Crime Unit tracks down serial killers and rapists using new techniques.</dd>
False 

https://www.filmaffinity.com/us/film339552.html
<dd class="" itemprop="description">SHOOTER is USA Network's new conspiracy thriller based on the best-selling novel "Point of Impact" by Stephen Hunter, and the 2007 Paramount film starring Mark Wahlberg. Starring Ryan Phillippe, the series follows the journey of Bob Lee Swagger, a highly-decorated veteran who is coaxed back into action to prevent a plot to kill the President. When Swagger's former commanding officer Isaac Johnson solicits his expertise in a clandestine operation, Swagger discovers that he is has been framed and must do everything in his power to protect his family and clear his name.</dd>
False 

https://www.filmaffinity.com/us/film786576.html
<dd class="" itemprop="description">TV Series (2014–2019). 5 seasons. 100 episodes. 

<dd class="" itemprop="description">Daisy O'Brien has to live a double life, after she was bitten by her vampire perents in order to save her life.</dd>
False 

https://www.filmaffinity.com/us/film120015.html
<dd class="" itemprop="description">TV Series (2016-2020). D.J. Tanner-Fuller is a widow and mother of three. Things become too much to handle, so she asks for help from her sister Stephanie and her best-friend Kimmy in this 13-episode spinoff of ABC classic “Full House.” While most of the first series’ cast is returning, this story focuses on Candace Cameron Bure’s DJ Tanner-Fuller. Now a veterinarian and also a widow, DJ calls upon her extended family to help raise her children — the rebellious 12-year-old Jackson (Michael Champion), neurotic 7-year-old Max (Elias Harger) and her newborn baby, Tommy Jr (played by twins).</dd>
False 

https://www.filmaffinity.com/us/film112263.html
<dd class="" itemprop="description">With a little help from his brother and accomplice, Tim, Boss B

<dd class="" itemprop="description">A medical student who becomes a zombie joins a Coroner's Office in order to gain access to the brains she must reluctantly eat so that she can maintain her humanity. But for every brain she eats, she also inherits their memories. Now she uses her abilities to solve their deaths with help from the Medical examiner and a police detective.</dd>
False 

https://www.filmaffinity.com/us/film538285.html
<dd class="" itemprop="description">The Garfield Show centers mainly on Garfield's usual antics and frolics, usually in function of his laziness and gluttony. It focuses on his quirky misadventures (often significantly darker, scarier and/or more bizarre than those found in the comic strip or previous animated adaptations), while always highlighting the fat cat's love for lasagna. Garfield lives with his owner, Jon Arbuckle, and his owner's dog, Odie, in a detached two story house (as opposed to the one story house in the comics and Garfield and Friends). Th

...

<dd class="" itemprop="description">Ambientada tras la caída del Imperio y antes de la aparición de la Primera Orden, la serie sigue los pasos de Mando, un cazarecompensas perteneciente a la legendaria tribu de los Mandalorian, un pistolero solitario que trabaja en los confines de la galaxia, donde no alcanza la autoridad de la Nueva República. (FILMAFFINITY) </dd>
False 

https://www.filmaffinity.com/es/film586817.html
<dd class="" itemprop="description">“Tras los pasos del elefante" sigue a los documentalistas en su grabación del épico viaje de los elefantes africanos por el desierto del Kalahari en el documental de Disneynature "Los elefantes". El equipo se enfrenta a condiciones extremas, terrenos inaccesibles, aguas infestadas de cocodrilos y encuentros con leones para poder mostrarnos cómo son estas criaturas tan magníficas y sus migraciones tradicionales.</dd>
False 

https://www.filmaffinity.com/es/film916496.html
<dd class="" itemprop="description">Forky comparte su idea de lo

<dd class="" itemprop="description">Una niña terrestre se siente una extraña en un colegio de alienígenas.</dd>
False 

https://www.filmaffinity.com/es/film274644.html
<dd class="" itemprop="description">Un romance en ciernes provoca un encuentro con unos duendes. </dd>
False 

https://www.filmaffinity.com/es/film177387.html
<dd class="" itemprop="description">Los pensamientos de un niño se revelan mientras está en el cole.</dd>
False 

https://www.filmaffinity.com/es/film211384.html
<dd class="" itemprop="description">La propuesta de "Cycles" gira en torno al verdadero significado de crear un hogar y todo lo que alberga en su interior. Es el primer cortometraje de Disney dentro del universo de la Realidad Virtual. (FILMAFFINITY)</dd>
False 

https://www.filmaffinity.com/es/film251062.html
<dd class="" itemprop="description">Un niño captura un rayo en un bote como proyecto para la feria de ciencias.</dd>
False 

https://www.filmaffinity.com/es/film644211.html
<dd class="" itemprop="des

<dd class="" itemprop="description">Biopic sobre la aclamada poeta norteamericana Emily Dickinson que explora los conflictos sociales, familiares y de género que sufrió la autora. (FILMAFFINITY)<br/>
<br/>
Estreno: 1 de noviembre en Apple TV+.<br/>
</dd>
False 

https://www.filmaffinity.com/es/film349292.html
<dd class="" itemprop="description">Cuando un fantasma se aparece en una librería del vecindario y comienza a liberar personajes de ficción en el mundo real, cuatro chicos deben unirse para resolver un emocionante misterio sobre los asuntos pendientes que tiene el fantasma.</dd>
False 

https://www.filmaffinity.com/es/film748109.html
<dd class="" itemprop="description">La serie explora lo que habría ocurrido si la carrera espacial mundial nunca hubiera terminado y la Unión Soviética hubiera conseguido superar a Estados Unidos como el primer país en poner a un hombre en la Luna.<br/>
</dd>
False 

https://www.filmaffinity.com/es/film248229.html
<dd class="" itemprop="description">C

https://www.filmaffinity.com/es/film508846.html
<dd class="" itemprop="description">Cuenta la historia real del joven abogado Bryan Stevenson (Jordan) y de su histórica batalla por la justicia. Después de licenciarse en Harvard, Bryan recibe ofertas de trabajo muy lucrativas. Pero él prefiere poner rumbo a Alabama para defender a personas que han sido condenadas erróneamente o que carecían de recursos para tener una representación legal adecuada, y lo hace con el apoyo de la activista local Eva Ansley (Larson). Uno de sus primeros y más turbulentos casos es el de Walter McMillian (Foxx), que en 1987 fue sentenciado a la pena muerte por el asesinato de una chica de 18 años, a pesar de que las pruebas demostraban ostensiblemente su inocencia. En los años posteriores, Bryan se ve envuelto en un laberinto de maniobras legales y políticas y de un racismo abierto y descarado mientras lucha por Walter y otros como él, a pesar de tenerlo todo en su contra, incluido el sistema legal.</dd>
False

<dd class="" itemprop="description">Un joven estudiante que desea vengar la muerte de su madre realiza un pacto con una orden secreta y se ve involucrado en una lucha entre hombres lobo y magos que hacen uso de la magia negra. (FILMAFFINITY)</dd>
False 

https://www.filmaffinity.com/es/film953955.html
<dd class="" itemprop="description">Un drama de fantasía y romance en el que una deidad ha desencadenado un demonio al mundo de los humanos, y ese demonio ha abierto la puerta a un mundo paralelo. Uno se parece a la Corea moderna tal como la conocemos, mientras que el otro es un universo alternativo en el que Corea es un imperio gobernado por un solo monarca. Para luchar contra el mal y cerrar la puerta entre sus dos mundos, el gobernante del Imperio coreano, Lee Gon, termina uniendo fuerzas con la detective Jung Tae Eul, que reside en la actual Corea.</dd>
False 

https://www.filmaffinity.com/es/film826923.html
<dd class="" itemprop="description">La Habana, principios de los 90. René Gon

In [14]:
len(description)

2383

In [15]:
df['Description'] = description
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  
0                                               None  
1  The world's most wanted criminal, Thomas Raymo...  
2  Macarena Ferreiro is a young naive woman who f...  
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....  
4  'Thirteen Reasons Why', based on the best-sell...

In [56]:
# Repeat the process in order to get the information from NaN values

for item in df.index:
    if df.Description[item] == 'NaN':
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # description
        print(soupFilm.find('dd', itemprop='description'))
        print((soupFilm.find('dd', itemprop='description')) == None, '\n')
    
        if (soupFilm.find('dd', itemprop='description')) != None:
            df.Description[item] = soupFilm.find('dd', itemprop='description').string
        else:
            df.Description[item] = 'NaN'

https://www.filmaffinity.com/us/film879405.html
<dd class="" itemprop="description">TV Series (2017-Present Day). 4 Seasons. A mysterious character called the Professor is planning the biggest robbery in history. To do this, he recruits eight thieves who take hostages and lock themselves in the Royal Mint of Spain as The Professor manipulates the police to carry out his plan from the outside. This group of very peculiar robbers have a plan: assault the Factory of Moneda and Timbre to carry out the most perfect robbery in the history of Spain and taking home 2,400 million euros.<br/>
<br/>
Release date Season 4: april 2020.</dd>
False 

https://www.filmaffinity.com/us/film103430.html
<dd class="" itemprop="description">TV Series. A missing child sets four families on a frantic hunt for answers. Their search for a culprit unearths a small town’s sins and secrets.<br/>
<br/>
Season 3 on Netflix:  27 June 2020<br/>
</dd>
False 

https://www.filmaffinity.com/us/film539830.html
<dd class="" 

False 

https://www.filmaffinity.com/us/film292512.html
<dd class="" itemprop="description">TV Series (2018-2020) 33 Episodes. 3 Seasons. The outward perfection of a family-run flower business hides a dark side rife with dysfunctional secrets in this darkly humorous comedy series.<br/>
<br/>
</dd>
False 

https://www.filmaffinity.com/us/film900221.html
<dd class="" itemprop="description">TV Series (2018-2019). 2 Seasons. 22 episodes. A disgraced, dissatisfied civil lawyer-turned-beauty pageant coach takes on a vengeful, bullied teenager as his client and has no idea what he's about to unleash upon the world. <br/>
<br/>
On february 2020 it was cancelled by Netflix.          </dd>
False 

https://www.filmaffinity.com/us/film233858.html
<dd class="" itemprop="description">Orange Is the New Black revolves around Piper Chapman (Taylor Schilling), a woman from Connecticut living in New York City, who is sentenced to 15 months in a women's federal prison in Litchfield, NY, for transporting a

<dd class="" itemprop="description">Hawkins, Indiana, in the 80s. When a young boy vanishes, the small town uncovers a mystery involving secret experiments, terrifying supernatural forces and one strange little girl.<br/>
<br/>
Second season will begin nearly a year after the first installment. </dd>
False 

https://www.filmaffinity.com/us/film589817.html
<dd class="" itemprop="description">TV Series (2017-2020). 5 Seasons. Set in the 1920s, this is the story of four women from different backgrounds newly hired as operators for a phone company. Madrid during 1928. The national telephone company opens its headquarters in the city centre and hundreds of girls queue up to get a job as a “cable girl” in the only place that represents progress and modernity for women at the time. Four girls, coming from very different backgrounds, will start work as operators. From that day on, jealousy, envy and betrayal will get mixed up with the hunger for success, friendship and love.<br/>
<br/>
Latest 

<dd class="" itemprop="description">Hyakkaou Private Academy. An institution for the privileged with a very peculiar curriculum. You see, when you're the sons and daughters of the wealthiest of the wealthy, it's not athletic prowess or book smarts that keep you ahead. It's reading your opponent, the art of the deal. What better way to hone those skills than with a rigorous curriculum of gambling? At Hyakkaou Private Academy, the winners live like kings, and the losers are put through the wringer. But when Yumeko Jabami enrolls, she's gonna teach these kids what a high roller really looks like!<br/>
</dd>
False 

https://www.filmaffinity.com/us/film871300.html
<dd class="" itemprop="description">InuYasha is the story of a dog half-demon who is constantly after a jewel of immense power, the Shikon jewel, also no as the Shikon no tama. He lives in the forest near the village where the jewel is protected by a priestess named Kikyo. Soon InuYasha and Kikyo fall in love and InuYasha promises

<dd class="" itemprop="description">Yuki's earliest memory is of a stormy night in winter, wherein she was attacked by a vampire... And then rescued by another. Now 10 years later, Yuki Cross, the adopted daughter of the headmaster of Cross Academy, has grown up and become a guardian of the vampire race, protecting her savior, Kaname, from discovery as he leads a group of vampires at the elite boarding school. But also at her side is Zero Kiryu, a childhood friend who’s hatred for the creatures that destroyed everything he held dear, is now determined never to trust them. This coexisting arrangement seems all well and good, but have the vampires truly renounced their murderous ways, or is there a darker truth behind their actions. Is Kaname's infatuation with Yuki the beginning of a forbidden romance, or is it something in her forgotten past that draws him to her. Because in this world of secrets, nothing is as it seems. And the price of misplaced trust may even be worse than death.<br

...

<dd class="" itemprop="description">Serie de TV (10 episodios). Cuenta con entrevistas y puntos de vista de los propios jugadores, seleccionadores y diferentes personalidades del mundo del fútbol. La serie documental tiene como objetivo adentrarse en el evento deportivo más grande jamás visto y mostrar, meses antes de que empiece el Mundial de Rusia 2018, la parte más desconocida de éste.<br/>
<br/>
</dd>
False 

https://www.filmaffinity.com/es/film334848.html
<dd class="" itemprop="description">La inspectora Robin Griffin acaba de regresar a Sydney e intenta recuperar las riendas de su vida. Cuando las olas llevan hasta la playa de Bondi el cuerpo de una joven asiática, las esperanzas de desenmascarar a su asesino se antojan remotas. Hasta que Robin descubre que la víctima no murió sola... Aunque Robin ve en esta investigación un camino para reconstruirse, rápidamente quedará atrapada por preocupaciones de carácter personal. Perseguida por el recuerdo del niño que abandonó al nacer, t

https://www.filmaffinity.com/es/film223568.html
<dd class="" itemprop="description">Una reevisión contemporánea del "Measure for Measure" de Shakespeare. Surge un romance improbable entre una inmigrante musulmana y un joven músico, postulándose en contra de los notorios departamentos de comisiones de Melbourne, donde reina un mundo de crimen, drogas y falta de armonía racial.<br/>
</dd>
False 

https://www.filmaffinity.com/es/film839954.html
<dd class="" itemprop="description">50 años después de la mítica llegada del hombre a la Luna, Solan y Eri se embarcan en una aventura espacial para dar el segundo paso sobre la Luna. Con la ayuda de su amigo inventor y de ingeniosas herramientas, ¿conseguirán construir su nave y llegar al espacio?<br/>
<br/>
</dd>
False 

https://www.filmaffinity.com/es/film379145.html
<dd class="" itemprop="description">La película gira en torno a una familia burguesa que posee una empresa en Calais, al lado de los campamentos donde viven miles de refugiados. (FI

<dd class="" itemprop="description">Miniserie de cinco capítulos de unos 15-20 minutos de duración, cada uno de ellos autoconclusivo, realizados durante el confinamiento de la primavera de 2020. Dirigidos a distancia por sus directores y protagonizados por actores que además hicieron de realizadores, técnicos, maquilladores y sonidistas. <br/>
<br/>
Los 5 relatos: <br/>
<br/>
- 'Selftape', una comedia romántica escrita y dirigida por Álvaro Fernández Armero y protagonizada por Sara Sálamo e Isco Alarcón.<br/>
<br/>
- 'Emparedados' de Fernando Colomo, un thriller que roza el terror, protagonizado por Manuela Velasco y Rafa Castejón.<br/>
<br/>
- 'El aprendiz', una comedia negra escrita y dirigida por David Marqués, protagonizada por Álvaro Rico y Carlos Bardem.<br/>
<br/>
- 'Finlandia' de Miguel Bardem, una historia romántica con Alberto Ammann y Clara Méndez-Leite.<br/>
<br/>
- 'Gourmet', thriller dirigido por Juan Diego Botto, protagonizado por Luis Tosar y María Luisa Mayol.</dd>
Fal

<dd class="" itemprop="description">La historia que se centra en la familia Tavner, donde el padre, Tom Tavner, es el Director de Inteligencia del Departamento de Estado de Estados Unidos. Su hijo mayor, Edward, es un miembro del senado, mientras que el pequeño John es un veterano de la guerra de Iraq. Para controlar su estrés John encuentra en la música folk una manera de eludir los traumas originados por su participación en el conflicto, aunque las letras de las canciones que compone desvelan, a veces, demasiados detalles de su "trabajo". (FILMAFFINITY)<br/>
</dd>
False 

https://www.filmaffinity.com/es/film538230.html
<dd class="" itemprop="description">Serie de TV (2017-actualidad). 4 temporadas. 46 episodios. Serie sobre las extravagantes vidas y amores de las responsables de una revista femenina global, Scarlet. La generación emergente de mujeres Scarlet se apoyan unas a otras mientras buscan sus propias voces en un mar de intimidantes líderes. Juntas exploran sexualidad, intimid

https://www.filmaffinity.com/es/film474882.html
<dd class="" itemprop="description">¿Qué sucede cuando las personas en las que confías demuestran ser deshonestas? 'The Morning Show' narra la caída libre de un informativo matutino a raíz de un escándalo, y su lucha por sobrevivir en una era en la que las noticias llegan en la palma de tu mano.<br/>
<br/>
</dd>
False 

https://www.filmaffinity.com/es/film988714.html
<dd class="" itemprop="description">Biopic sobre la aclamada poeta norteamericana Emily Dickinson que explora los conflictos sociales, familiares y de género que sufrió la autora. (FILMAFFINITY)<br/>
<br/>
Estreno: 1 de noviembre en Apple TV+.<br/>
</dd>
False 

https://www.filmaffinity.com/es/film748109.html
<dd class="" itemprop="description">La serie explora lo que habría ocurrido si la carrera espacial mundial nunca hubiera terminado y la Unión Soviética hubiera conseguido superar a Estados Unidos como el primer país en poner a un hombre en la Luna.<br/>
</dd>
False 

htt

In [57]:
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  
0  TV Series (2017-Present Day). 4 Seasons. A mys...  
1  The world's most wanted criminal, Thomas Raymo...  
2  Macarena Ferreiro is a young naive woman who f...  
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....  
4  'Thirteen Reasons Why', based on the best-sell...

In [33]:
# Repeat the process in order to get the information from NaN values

for item in df.index:
    if df.Description[item] == None: # en aquest cas el text es guarda com 'None'
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # description
        print(soupFilm.find('dd', itemprop='description'))
        print((soupFilm.find('dd', itemprop='description')) == None, '\n')
    
        if (soupFilm.find('dd', itemprop='description')) != None:
            df.Description[item] = soupFilm.find('dd', itemprop='description').text
            # he posat .text enlloc de .string perquè agafés bé la descripció
        else:
            df.Description[item] = 'NaN'

https://www.filmaffinity.com/es/film452096.html
None
True 

no


In [58]:
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  
0  TV Series (2017-Present Day). 4 Seasons. A mys...  
1  The world's most wanted criminal, Thomas Raymo...  
2  Macarena Ferreiro is a young naive woman who f...  
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....  
4  'Thirteen Reasons Why', based on the best-sell...

In [59]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the rating average

In [73]:
ratingAverage = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # rating average
    print(soupFilm.find('div', itemprop='ratingValue'))
    print((soupFilm.find('div', itemprop='ratingValue'))==None, '\n')
    
    if (soupFilm.find('div', itemprop='ratingValue')) != None:
        num = soupFilm.find('div', itemprop='ratingValue').string
        num = num.replace('\n                        ','')
        num = num.replace('                    ','')
        num = num.replace(',','.')
        num = float(num)
        ratingAverage.append(num)
    else:
        ratingAverage.append(np.nan)

https://www.filmaffinity.com/us/film879405.html
<div content="7.1" id="movie-rat-avg" itemprop="ratingValue">
                        7.1                    </div>
False 

https://www.filmaffinity.com/us/film573633.html
<div content="6.4" id="movie-rat-avg" itemprop="ratingValue">
                        6.4                    </div>
False 

https://www.filmaffinity.com/us/film441483.html
<div content="7" id="movie-rat-avg" itemprop="ratingValue">
                        7.0                    </div>
False 

https://www.filmaffinity.com/us/film822756.html
<div content="7.3" id="movie-rat-avg" itemprop="ratingValue">
                        7.3                    </div>
False 

https://www.filmaffinity.com/us/film999360.html
<div content="6.8" id="movie-rat-avg" itemprop="ratingValue">
                        6.8                    </div>
False 

https://www.filmaffinity.com/us/film103430.html
<div content="7.6" id="movie-rat-avg" itemprop="ratingValue">
                        7.6     

<div content="8" id="movie-rat-avg" itemprop="ratingValue">
                        8.0                    </div>
False 

https://www.filmaffinity.com/us/film333607.html
<div content="7.7" id="movie-rat-avg" itemprop="ratingValue">
                        7.7                    </div>
False 

https://www.filmaffinity.com/us/film671612.html
<div content="7.2" id="movie-rat-avg" itemprop="ratingValue">
                        7.2                    </div>
False 

https://www.filmaffinity.com/us/film464489.html
<div content="8" id="movie-rat-avg" itemprop="ratingValue">
                        8.0                    </div>
False 

https://www.filmaffinity.com/us/film397789.html
<div content="4.9" id="movie-rat-avg" itemprop="ratingValue">
                        4.8                    </div>
False 

https://www.filmaffinity.com/us/film332824.html
<div content="6.1" id="movie-rat-avg" itemprop="ratingValue">
                        6.1                    </div>
False 

https://www.filmaffi

<div content="7.3" id="movie-rat-avg" itemprop="ratingValue">
                        7.2                    </div>
False 

https://www.filmaffinity.com/us/film388413.html
<div content="5.5" id="movie-rat-avg" itemprop="ratingValue">
                        5.5                    </div>
False 

https://www.filmaffinity.com/us/film234251.html
<div content="6.9" id="movie-rat-avg" itemprop="ratingValue">
                        6.9                    </div>
False 

https://www.filmaffinity.com/us/film566200.html
<div content="6.1" id="movie-rat-avg" itemprop="ratingValue">
                        6.1                    </div>
False 

https://www.filmaffinity.com/us/film646609.html
<div content="7.5" id="movie-rat-avg" itemprop="ratingValue">
                        7.5                    </div>
False 

https://www.filmaffinity.com/us/film733108.html
<div content="7.1" id="movie-rat-avg" itemprop="ratingValue">
                        7.1                    </div>
False 

https://www.film

<div content="6.8" id="movie-rat-avg" itemprop="ratingValue">
                        6.8                    </div>
False 

https://www.filmaffinity.com/us/film238789.html
<div content="5.1" id="movie-rat-avg" itemprop="ratingValue">
                        5.1                    </div>
False 

https://www.filmaffinity.com/us/film982098.html
None
True 

https://www.filmaffinity.com/us/film935438.html
<div content="7.7" id="movie-rat-avg" itemprop="ratingValue">
                        7.7                    </div>
False 

https://www.filmaffinity.com/us/film444396.html
<div content="5.9" id="movie-rat-avg" itemprop="ratingValue">
                        5.9                    </div>
False 

https://www.filmaffinity.com/us/film499162.html
<div content="4.6" id="movie-rat-avg" itemprop="ratingValue">
                        4.6                    </div>
False 

https://www.filmaffinity.com/us/film109990.html
<div content="3.5" id="movie-rat-avg" itemprop="ratingValue">
                  

<div content="3.4" id="movie-rat-avg" itemprop="ratingValue">
                        3.4                    </div>
False 

https://www.filmaffinity.com/us/film384644.html
<div content="7.9" id="movie-rat-avg" itemprop="ratingValue">
                        7.9                    </div>
False 

https://www.filmaffinity.com/us/film916461.html
<div content="8.3" id="movie-rat-avg" itemprop="ratingValue">
                        8.3                    </div>
False 

https://www.filmaffinity.com/us/film315845.html
<div content="6.8" id="movie-rat-avg" itemprop="ratingValue">
                        6.8                    </div>
False 

https://www.filmaffinity.com/us/film500190.html
<div content="6.5" id="movie-rat-avg" itemprop="ratingValue">
                        6.5                    </div>
False 

https://www.filmaffinity.com/us/film729626.html
<div content="7.9" id="movie-rat-avg" itemprop="ratingValue">
                        7.9                    </div>
False 

https://www.film

...

<div content="3.2" id="movie-rat-avg" itemprop="ratingValue">
                        3,2                    </div>
False 

https://www.filmaffinity.com/es/film988821.html
<div content="6.7" id="movie-rat-avg" itemprop="ratingValue">
                        6,7                    </div>
False 

https://www.filmaffinity.com/es/film875162.html
<div content="6.7" id="movie-rat-avg" itemprop="ratingValue">
                        6,7                    </div>
False 

https://www.filmaffinity.com/es/film165249.html
<div content="6.8" id="movie-rat-avg" itemprop="ratingValue">
                        6,8                    </div>
False 

https://www.filmaffinity.com/es/film547835.html
<div content="5.8" id="movie-rat-avg" itemprop="ratingValue">
                        5,8                    </div>
False 

https://www.filmaffinity.com/es/film612466.html
<div content="5.5" id="movie-rat-avg" itemprop="ratingValue">
                        5,5                    </div>
False 

https://www.film

<div content="7.2" id="movie-rat-avg" itemprop="ratingValue">
                        7,2                    </div>
False 

https://www.filmaffinity.com/es/film871805.html
<div content="7.1" id="movie-rat-avg" itemprop="ratingValue">
                        7,1                    </div>
False 

https://www.filmaffinity.com/es/film244943.html
<div content="6.6" id="movie-rat-avg" itemprop="ratingValue">
                        6,6                    </div>
False 

https://www.filmaffinity.com/es/film395470.html
<div content="6.3" id="movie-rat-avg" itemprop="ratingValue">
                        6,3                    </div>
False 

https://www.filmaffinity.com/es/film903885.html
None
True 

https://www.filmaffinity.com/es/film294612.html
<div content="6" id="movie-rat-avg" itemprop="ratingValue">
                        6,0                    </div>
False 

https://www.filmaffinity.com/es/film704931.html
<div content="6.1" id="movie-rat-avg" itemprop="ratingValue">
                    

<div content="5.6" id="movie-rat-avg" itemprop="ratingValue">
                        5,6                    </div>
False 

https://www.filmaffinity.com/es/film280367.html
<div content="6.7" id="movie-rat-avg" itemprop="ratingValue">
                        6,7                    </div>
False 

https://www.filmaffinity.com/es/film305160.html
<div content="5.8" id="movie-rat-avg" itemprop="ratingValue">
                        5,8                    </div>
False 

https://www.filmaffinity.com/es/film837340.html
<div content="4.9" id="movie-rat-avg" itemprop="ratingValue">
                        4,9                    </div>
False 

https://www.filmaffinity.com/es/film119391.html
None
True 

https://www.filmaffinity.com/es/film916911.html
<div content="4.4" id="movie-rat-avg" itemprop="ratingValue">
                        4,4                    </div>
False 

https://www.filmaffinity.com/es/film297318.html
<div content="5.5" id="movie-rat-avg" itemprop="ratingValue">
                  

None
True 

https://www.filmaffinity.com/es/film544948.html
<div content="7.7" id="movie-rat-avg" itemprop="ratingValue">
                        7,7                    </div>
False 

https://www.filmaffinity.com/es/film586817.html
None
True 

https://www.filmaffinity.com/es/film916496.html
<div content="4.7" id="movie-rat-avg" itemprop="ratingValue">
                        4,7                    </div>
False 

https://www.filmaffinity.com/es/film785562.html
None
True 

https://www.filmaffinity.com/es/film230922.html
<div content="7" id="movie-rat-avg" itemprop="ratingValue">
                        7,0                    </div>
False 

https://www.filmaffinity.com/es/film371085.html
<div content="5.1" id="movie-rat-avg" itemprop="ratingValue">
                        5,1                    </div>
False 

https://www.filmaffinity.com/es/film720391.html
<div content="5.5" id="movie-rat-avg" itemprop="ratingValue">
                        5,5                    </div>
False 

https://ww

<div content="7.3" id="movie-rat-avg" itemprop="ratingValue">
                        7,3                    </div>
False 

https://www.filmaffinity.com/es/film166366.html
<div content="6.9" id="movie-rat-avg" itemprop="ratingValue">
                        6,8                    </div>
False 

https://www.filmaffinity.com/es/film988714.html
<div content="6.2" id="movie-rat-avg" itemprop="ratingValue">
                        6,2                    </div>
False 

https://www.filmaffinity.com/es/film349292.html
<div content="4.8" id="movie-rat-avg" itemprop="ratingValue">
                        4,8                    </div>
False 

https://www.filmaffinity.com/es/film748109.html
<div content="6.6" id="movie-rat-avg" itemprop="ratingValue">
                        6,6                    </div>
False 

https://www.filmaffinity.com/es/film248229.html
None
True 

https://www.filmaffinity.com/es/film683886.html
<div content="6.7" id="movie-rat-avg" itemprop="ratingValue">
                  

In [74]:
len(ratingAverage)

2383

In [75]:
df['RatingAverage'] = ratingAverage
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  RatingAverage  
0  TV Series (2017-Present Day). 4 Seasons. A mys...            7.1  
1  The world's most wanted criminal, Thomas Raymo...            6.4  
2  Macarena Ferreiro is a young naive woman who f...            7.0  
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....            7.3  
4  'Thirteen Reasons Why', based on the best-sell...            6.8

In [76]:
# Repeat the process in order to get the information from NaN values

for item in df.index:
    if np.isnan(df.RatingAverage[item]):
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # rating average
        print(soupFilm.find('div', itemprop='ratingValue'))
        print((soupFilm.find('div', itemprop='ratingValue'))==None, '\n')
    
        if (soupFilm.find('div', itemprop='ratingValue')) != None:
            num = soupFilm.find('div', itemprop='ratingValue').string
            num = num.replace('\n                        ','')
            num = num.replace('                    ','')
            num = num.replace(',','.')
            num = float(num)
            df.RatingAverage[item] = num
        else:
            df.RatingAverage[item] = np.nan

https://www.filmaffinity.com/us/film244225.html
None
True 

https://www.filmaffinity.com/us/film354270.html


/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


None
True 

https://www.filmaffinity.com/us/film809007.html
None
True 

https://www.filmaffinity.com/us/film730817.html
None
True 

https://www.filmaffinity.com/us/film846678.html
None
True 

https://www.filmaffinity.com/us/film655884.html
None
True 

https://www.filmaffinity.com/us/film682334.html
None
True 

https://www.filmaffinity.com/us/film612105.html
None
True 

https://www.filmaffinity.com/us/film431658.html
None
True 

https://www.filmaffinity.com/us/film835052.html
None
True 

https://www.filmaffinity.com/us/film982098.html
None
True 

https://www.filmaffinity.com/us/film177836.html
None
True 

https://www.filmaffinity.com/us/film107452.html
None
True 

https://www.filmaffinity.com/us/film655260.html
None
True 

https://www.filmaffinity.com/us/film516268.html
None
True 

https://www.filmaffinity.com/us/film951448.html
None
True 

https://www.filmaffinity.com/us/film812084.html
None
True 

https://www.filmaffinity.com/us/film256850.html
None
True 

https://www.filmaffinity.com

/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


<div content="3.8" id="movie-rat-avg" itemprop="ratingValue">
                        3,8                    </div>
False 

https://www.filmaffinity.com/es/film121857.html
<div content="4.8" id="movie-rat-avg" itemprop="ratingValue">
                        4,8                    </div>
False 

https://www.filmaffinity.com/us/film813543.html
<div content="4.9" id="movie-rat-avg" itemprop="ratingValue">
                        4.9                    </div>
False 

https://www.filmaffinity.com/us/film228841.html
<div content="5.9" id="movie-rat-avg" itemprop="ratingValue">
                        5.9                    </div>
False 

https://www.filmaffinity.com/es/film772178.html
<div content="7.1" id="movie-rat-avg" itemprop="ratingValue">
                        7,1                    </div>
False 

https://www.filmaffinity.com/us/film830776.html
None
True 

https://www.filmaffinity.com/es/film167911.html
<div content="4.1" id="movie-rat-avg" itemprop="ratingValue">
                  

True 

https://www.filmaffinity.com/es/film671939.html
<div content="6" id="movie-rat-avg" itemprop="ratingValue">
                        6,0                    </div>
False 

https://www.filmaffinity.com/us/film835197.html
None
True 

https://www.filmaffinity.com/es/film920458.html
<div content="6.5" id="movie-rat-avg" itemprop="ratingValue">
                        6,5                    </div>
False 

https://www.filmaffinity.com/es/film799971.html
None
True 

https://www.filmaffinity.com/es/film602721.html
None
True 

https://www.filmaffinity.com/es/film515740.html
<div content="6.9" id="movie-rat-avg" itemprop="ratingValue">
                        6,9                    </div>
False 

https://www.filmaffinity.com/es/film438583.html
<div content="7.1" id="movie-rat-avg" itemprop="ratingValue">
                        7,1                    </div>
False 

https://www.filmaffinity.com/us/film669856.html
<div content="5.1" id="movie-rat-avg" itemprop="ratingValue">
                 

<div content="7" id="movie-rat-avg" itemprop="ratingValue">
                        7,0                    </div>
False 

https://www.filmaffinity.com/es/film562470.html
<div content="3.7" id="movie-rat-avg" itemprop="ratingValue">
                        3,7                    </div>
False 

https://www.filmaffinity.com/es/film257814.html
<div content="5.1" id="movie-rat-avg" itemprop="ratingValue">
                        5,1                    </div>
False 

https://www.filmaffinity.com/es/film679356.html
<div content="4.5" id="movie-rat-avg" itemprop="ratingValue">
                        4,5                    </div>
False 

https://www.filmaffinity.com/es/film857434.html
<div content="6.6" id="movie-rat-avg" itemprop="ratingValue">
                        6,6                    </div>
False 

https://www.filmaffinity.com/es/film594689.html
None
True 

https://www.filmaffinity.com/es/film793070.html
<div content="6.4" id="movie-rat-avg" itemprop="ratingValue">
                    

<div content="4.6" id="movie-rat-avg" itemprop="ratingValue">
                        4,6                    </div>
False 

https://www.filmaffinity.com/es/film758290.html
<div content="6.3" id="movie-rat-avg" itemprop="ratingValue">
                        6,3                    </div>
False 

https://www.filmaffinity.com/es/film243924.html
<div content="7.9" id="movie-rat-avg" itemprop="ratingValue">
                        7,8                    </div>
False 

https://www.filmaffinity.com/es/film971763.html
<div content="7.4" id="movie-rat-avg" itemprop="ratingValue">
                        7,4                    </div>
False 

https://www.filmaffinity.com/es/film632155.html
<div content="8.4" id="movie-rat-avg" itemprop="ratingValue">
                        8,4                    </div>
False 

https://www.filmaffinity.com/es/film108537.html
<div content="6.4" id="movie-rat-avg" itemprop="ratingValue">
                        6,4                    </div>
False 

https://www.film

<div content="5.9" id="movie-rat-avg" itemprop="ratingValue">
                        5,9                    </div>
False 

https://www.filmaffinity.com/es/film802561.html
<div content="6.9" id="movie-rat-avg" itemprop="ratingValue">
                        6,9                    </div>
False 

https://www.filmaffinity.com/es/film433939.html
<div content="5.1" id="movie-rat-avg" itemprop="ratingValue">
                        5,1                    </div>
False 

https://www.filmaffinity.com/es/film466494.html
<div content="5.8" id="movie-rat-avg" itemprop="ratingValue">
                        5,8                    </div>
False 

https://www.filmaffinity.com/es/film517559.html
<div content="5.2" id="movie-rat-avg" itemprop="ratingValue">
                        5,2                    </div>
False 

https://www.filmaffinity.com/es/film161408.html
<div content="6" id="movie-rat-avg" itemprop="ratingValue">
                        6,0                    </div>
False 

https://www.filmaf

<div content="6.8" id="movie-rat-avg" itemprop="ratingValue">
                        6,8                    </div>
False 

https://www.filmaffinity.com/es/film287081.html
<div content="5.9" id="movie-rat-avg" itemprop="ratingValue">
                        5,9                    </div>
False 

https://www.filmaffinity.com/es/film530592.html
<div content="6.1" id="movie-rat-avg" itemprop="ratingValue">
                        6,1                    </div>
False 

https://www.filmaffinity.com/es/film480815.html
<div content="4.6" id="movie-rat-avg" itemprop="ratingValue">
                        4,6                    </div>
False 

https://www.filmaffinity.com/es/film111213.html
<div content="6.2" id="movie-rat-avg" itemprop="ratingValue">
                        6,2                    </div>
False 

https://www.filmaffinity.com/es/film634164.html
<div content="6.5" id="movie-rat-avg" itemprop="ratingValue">
                        6,5                    </div>
False 

https://www.film

In [77]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the votes

In [85]:
votes = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # number of votes
    print(soupFilm.find('span', itemprop='ratingCount'))
    print((soupFilm.find('span', itemprop='ratingCount')) == None, '\n')
    
    if (soupFilm.find('span', itemprop='ratingCount')) != None:
        num = soupFilm.find('span', itemprop='ratingCount').string
        num = num.replace('.','')
        num = num.replace(',','')
        num = num.replace('\xa0','')
        num = int(num)
        votes.append(num)
    else:
        votes.append(np.nan)

https://www.filmaffinity.com/us/film879405.html
<span content="25691" itemprop="ratingCount">25,691</span>
False 

https://www.filmaffinity.com/us/film573633.html
<span content="5148" itemprop="ratingCount">5,148</span>
False 

https://www.filmaffinity.com/us/film441483.html
<span content="6941" itemprop="ratingCount">6,941</span>
False 

https://www.filmaffinity.com/us/film822756.html
<span content="71511" itemprop="ratingCount">71,511</span>
False 

https://www.filmaffinity.com/us/film999360.html
<span content="21496" itemprop="ratingCount">21,496</span>
False 

https://www.filmaffinity.com/us/film103430.html
<span content="18042" itemprop="ratingCount">18,042</span>
False 

https://www.filmaffinity.com/us/film910593.html
<span content="1901" itemprop="ratingCount">1,901</span>
False 

https://www.filmaffinity.com/us/film482516.html
<span content="1992" itemprop="ratingCount">1,992</span>
False 

https://www.filmaffinity.com/us/film539830.html
<span content="26208" itemprop="ratingCo

<span content="185" itemprop="ratingCount">185</span>
False 

https://www.filmaffinity.com/us/film959114.html
<span content="29604" itemprop="ratingCount">29,604</span>
False 

https://www.filmaffinity.com/us/film126513.html
<span content="488" itemprop="ratingCount">488</span>
False 

https://www.filmaffinity.com/us/film699539.html
<span content="24" itemprop="ratingCount">24</span>
False 

https://www.filmaffinity.com/us/film120015.html
<span content="892" itemprop="ratingCount">892</span>
False 

https://www.filmaffinity.com/us/film112263.html
<span content="297" itemprop="ratingCount">297</span>
False 

https://www.filmaffinity.com/us/film322094.html
<span content="747" itemprop="ratingCount">747</span>
False 

https://www.filmaffinity.com/us/film549763.html
<span content="5134" itemprop="ratingCount">5,134</span>
False 

https://www.filmaffinity.com/us/film863889.html
<span content="66" itemprop="ratingCount">66</span>
False 

https://www.filmaffinity.com/us/film329238.html
<span 

None
True 

https://www.filmaffinity.com/us/film935438.html
<span content="12942" itemprop="ratingCount">12,942</span>
False 

https://www.filmaffinity.com/us/film444396.html
<span content="49" itemprop="ratingCount">49</span>
False 

https://www.filmaffinity.com/us/film499162.html
<span content="73" itemprop="ratingCount">73</span>
False 

https://www.filmaffinity.com/us/film109990.html
<span content="118" itemprop="ratingCount">118</span>
False 

https://www.filmaffinity.com/us/film723586.html
<span content="1399" itemprop="ratingCount">1,399</span>
False 

https://www.filmaffinity.com/us/film920440.html
<span content="7580" itemprop="ratingCount">7,580</span>
False 

https://www.filmaffinity.com/us/film504520.html
<span content="7122" itemprop="ratingCount">7,122</span>
False 

https://www.filmaffinity.com/us/film741087.html
<span content="51" itemprop="ratingCount">51</span>
False 

https://www.filmaffinity.com/us/film150299.html
<span content="6282" itemprop="ratingCount">6,282</s

<span content="748" itemprop="ratingCount">748</span>
False 

https://www.filmaffinity.com/us/film278491.html
<span content="12157" itemprop="ratingCount">12,157</span>
False 

https://www.filmaffinity.com/us/film700019.html
<span content="78" itemprop="ratingCount">78</span>
False 

https://www.filmaffinity.com/us/film101269.html
<span content="522" itemprop="ratingCount">522</span>
False 

https://www.filmaffinity.com/us/film188031.html
<span content="1395" itemprop="ratingCount">1,395</span>
False 

https://www.filmaffinity.com/us/film878660.html
<span content="148" itemprop="ratingCount">148</span>
False 

https://www.filmaffinity.com/us/film145548.html
<span content="2526" itemprop="ratingCount">2,526</span>
False 

https://www.filmaffinity.com/us/film565601.html
<span content="1076" itemprop="ratingCount">1,076</span>
False 

https://www.filmaffinity.com/us/film775929.html
<span content="66" itemprop="ratingCount">66</span>
False 

https://www.filmaffinity.com/us/film440387.html


None
True 

https://www.filmaffinity.com/us/film541055.html
None
True 

https://www.filmaffinity.com/us/film494373.html
None
True 

https://www.filmaffinity.com/us/film943736.html
None
True 

https://www.filmaffinity.com/us/film515522.html
None
True 

https://www.filmaffinity.com/us/film219474.html
None
True 

https://www.filmaffinity.com/us/film249767.html
None
True 

https://www.filmaffinity.com/us/film299957.html
None
True 

https://www.filmaffinity.com/us/film402563.html
None
True 

https://www.filmaffinity.com/us/film369843.html
None
True 

https://www.filmaffinity.com/us/film918117.html
None
True 

https://www.filmaffinity.com/us/film735633.html
None
True 

https://www.filmaffinity.com/us/film516268.html
None
True 

https://www.filmaffinity.com/us/film286333.html
None
True 

https://www.filmaffinity.com/us/film126739.html
None
True 

https://www.filmaffinity.com/us/film586098.html
None
True 

https://www.filmaffinity.com/us/film556666.html
<span content="11698" itemprop="ratingCo

...

<span content="1056" itemprop="ratingCount">1.056</span>
False 

https://www.filmaffinity.com/es/film860404.html
<span content="373" itemprop="ratingCount">373</span>
False 

https://www.filmaffinity.com/es/film755966.html
<span content="584" itemprop="ratingCount">584</span>
False 

https://www.filmaffinity.com/es/film743683.html
<span content="99" itemprop="ratingCount">99</span>
False 

https://www.filmaffinity.com/es/film147746.html
<span content="86" itemprop="ratingCount">86</span>
False 

https://www.filmaffinity.com/es/film168124.html
<span content="19585" itemprop="ratingCount">19.585</span>
False 

https://www.filmaffinity.com/es/film273774.html
None
True 

https://www.filmaffinity.com/es/film318913.html
<span content="21" itemprop="ratingCount">21</span>
False 

https://www.filmaffinity.com/es/film906832.html
<span content="521" itemprop="ratingCount">521</span>
False 

https://www.filmaffinity.com/es/film847376.html
<span content="191" itemprop="ratingCount">191</span>
Fals

<span content="338" itemprop="ratingCount">338</span>
False 

https://www.filmaffinity.com/es/film802561.html
<span content="331" itemprop="ratingCount">331</span>
False 

https://www.filmaffinity.com/es/film433939.html
<span content="382" itemprop="ratingCount">382</span>
False 

https://www.filmaffinity.com/es/film466494.html
<span content="218" itemprop="ratingCount">218</span>
False 

https://www.filmaffinity.com/es/film517559.html
<span content="422" itemprop="ratingCount">422</span>
False 

https://www.filmaffinity.com/es/film161408.html
<span content="84" itemprop="ratingCount">84</span>
False 

https://www.filmaffinity.com/es/film637623.html
<span content="36" itemprop="ratingCount">36</span>
False 

https://www.filmaffinity.com/es/film209323.html
<span content="71" itemprop="ratingCount">71</span>
False 

https://www.filmaffinity.com/es/film637249.html
<span content="73" itemprop="ratingCount">73</span>
False 

https://www.filmaffinity.com/es/film786463.html
<span content="120

<span content="220" itemprop="ratingCount">220</span>
False 

https://www.filmaffinity.com/es/film518411.html
<span content="476" itemprop="ratingCount">476</span>
False 

https://www.filmaffinity.com/es/film842259.html
<span content="61" itemprop="ratingCount">61</span>
False 

https://www.filmaffinity.com/es/film720439.html
<span content="5500" itemprop="ratingCount">5.500</span>
False 

https://www.filmaffinity.com/es/film979723.html
<span content="851" itemprop="ratingCount">851</span>
False 

https://www.filmaffinity.com/es/film529370.html
<span content="556" itemprop="ratingCount">556</span>
False 

https://www.filmaffinity.com/es/film404949.html
<span content="73" itemprop="ratingCount">73</span>
False 

https://www.filmaffinity.com/es/film956534.html
<span content="53" itemprop="ratingCount">53</span>
False 

https://www.filmaffinity.com/es/film212427.html
<span content="340" itemprop="ratingCount">340</span>
False 

https://www.filmaffinity.com/es/film800455.html
None
True 

h

<span content="3184" itemprop="ratingCount">3.184</span>
False 

https://www.filmaffinity.com/es/film264485.html
<span content="265" itemprop="ratingCount">265</span>
False 

https://www.filmaffinity.com/es/film409143.html
<span content="181" itemprop="ratingCount">181</span>
False 

https://www.filmaffinity.com/es/film867567.html
<span content="83" itemprop="ratingCount">83</span>
False 

https://www.filmaffinity.com/es/film485726.html
<span content="114" itemprop="ratingCount">114</span>
False 

https://www.filmaffinity.com/es/film262213.html
<span content="282" itemprop="ratingCount">282</span>
False 

https://www.filmaffinity.com/es/film871783.html
<span content="131" itemprop="ratingCount">131</span>
False 

https://www.filmaffinity.com/es/film532790.html
<span content="176" itemprop="ratingCount">176</span>
False 

https://www.filmaffinity.com/es/film657476.html
<span content="905" itemprop="ratingCount">905</span>
False 

https://www.filmaffinity.com/es/film828850.html
<span con

None
True 

https://www.filmaffinity.com/es/film821462.html
<span content="31" itemprop="ratingCount">31</span>
False 

https://www.filmaffinity.com/es/film764468.html
None
True 

https://www.filmaffinity.com/es/film246878.html
None
True 

https://www.filmaffinity.com/es/film576642.html
<span content="169" itemprop="ratingCount">169</span>
False 

https://www.filmaffinity.com/es/film455085.html
<span content="119" itemprop="ratingCount">119</span>
False 

https://www.filmaffinity.com/es/film937693.html
<span content="32" itemprop="ratingCount">32</span>
False 

https://www.filmaffinity.com/es/film239610.html
<span content="222" itemprop="ratingCount">222</span>
False 

https://www.filmaffinity.com/es/film671786.html
<span content="432" itemprop="ratingCount">432</span>
False 

https://www.filmaffinity.com/es/film707527.html
<span content="527" itemprop="ratingCount">527</span>
False 

https://www.filmaffinity.com/es/film734275.html
<span content="56" itemprop="ratingCount">56</span>
Fa

In [86]:
df['Votes'] = votes
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  RatingAverage    Votes  
0  TV Series (2017-Present Day). 4 Seasons. A mys...            7.1  25691.0  
1  The world's most wanted criminal, Thomas Raymo...            6.4   5148.0  
2  Macarena Ferreiro is a young naive woman who f...            7.0   6941.0  
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....            7.3  71511.0  
4  'Thirteen Reasons Why', based on the best-sell...            6.8  21496.0

In [88]:
# Repeat the process in order to get the information from NaN values

for item in df.index:
    if np.isnan(df.Votes[item]):
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # number of votes
        print(soupFilm.find('span', itemprop='ratingCount'))
        print((soupFilm.find('span', itemprop='ratingCount')) == None, '\n')
    
        if (soupFilm.find('span', itemprop='ratingCount')) != None:
            num = soupFilm.find('span', itemprop='ratingCount').string
            num = num.replace('.','')
            num = num.replace(',','')
            num = num.replace('\xa0','')
            num = int(num)
            df.Votes[item] = num
        else:
            df.Votes[item] = np.nan

https://www.filmaffinity.com/us/film244225.html
None
True 

https://www.filmaffinity.com/us/film354270.html


/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


None
True 

https://www.filmaffinity.com/us/film809007.html
None
True 

https://www.filmaffinity.com/us/film730817.html
None
True 

https://www.filmaffinity.com/us/film846678.html
None
True 

https://www.filmaffinity.com/us/film655884.html
None
True 

https://www.filmaffinity.com/us/film682334.html
None
True 

https://www.filmaffinity.com/us/film612105.html
None
True 

https://www.filmaffinity.com/us/film431658.html
None
True 

https://www.filmaffinity.com/us/film835052.html
None
True 

https://www.filmaffinity.com/us/film982098.html
None
True 

https://www.filmaffinity.com/us/film177836.html
None
True 

https://www.filmaffinity.com/us/film107452.html
None
True 

https://www.filmaffinity.com/us/film655260.html
None
True 

https://www.filmaffinity.com/us/film516268.html
None
True 

https://www.filmaffinity.com/us/film951448.html
None
True 

https://www.filmaffinity.com/us/film812084.html
None
True 

https://www.filmaffinity.com/us/film256850.html
None
True 

https://www.filmaffinity.com

/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


<span content="566" itemprop="ratingCount">566</span>
False 

https://www.filmaffinity.com/es/film867890.html
<span content="279" itemprop="ratingCount">279</span>
False 

https://www.filmaffinity.com/es/film359286.html
<span content="228" itemprop="ratingCount">228</span>
False 

https://www.filmaffinity.com/us/film877112.html
<span content="447" itemprop="ratingCount">447</span>
False 

https://www.filmaffinity.com/us/film553395.html
<span content="154" itemprop="ratingCount">154</span>
False 

https://www.filmaffinity.com/us/film998357.html
None
True 

https://www.filmaffinity.com/es/film594568.html
<span content="2040" itemprop="ratingCount">2.040</span>
False 

https://www.filmaffinity.com/es/film473535.html
<span content="1152" itemprop="ratingCount">1.152</span>
False 

https://www.filmaffinity.com/es/film502575.html
<span content="341" itemprop="ratingCount">341</span>
False 

https://www.filmaffinity.com/es/film419452.html
<span content="967" itemprop="ratingCount">967</span>


None
True 

https://www.filmaffinity.com/es/film990065.html
None
True 

https://www.filmaffinity.com/es/film356072.html
None
True 

https://www.filmaffinity.com/es/film528779.html
None
True 

https://www.filmaffinity.com/es/film764527.html
None
True 

https://www.filmaffinity.com/es/film277060.html
None
True 

https://www.filmaffinity.com/es/film467237.html
None
True 

https://www.filmaffinity.com/es/film307126.html
None
True 

https://www.filmaffinity.com/es/film223568.html
None
True 

https://www.filmaffinity.com/es/film948274.html
None
True 

https://www.filmaffinity.com/es/film711112.html
None
True 

https://www.filmaffinity.com/es/film273774.html
None
True 

https://www.filmaffinity.com/es/film560179.html
None
True 

https://www.filmaffinity.com/es/film840616.html
None
True 

https://www.filmaffinity.com/es/film143305.html
None
True 

https://www.filmaffinity.com/es/film452096.html
None
True 

https://www.filmaffinity.com/es/film511574.html
None
True 

https://www.filmaffinity.com

In [89]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')

#### Scrapping the reviews

In [90]:
reviews = []
reviewsComplete = []

for link in df.Link:
    print(link)
    film = requests.get(link)
    soupFilm = BeautifulSoup(film.text, 'html.parser')
    
    # reviews
    if (len(soupFilm.find_all('ul', id='pro-reviews')) != 0) == True:
        
        print(soupFilm.find_all('ul', id='pro-reviews')[0].find('em'))
        print((soupFilm.find_all('ul', id='pro-reviews')[0].find('em')) == None, '\n')
        
        if (soupFilm.find_all('ul', id='pro-reviews')[0].find('em')) != None:
            filmReviews = requests.get(soupFilm.find_all('ul', id='pro-reviews')[0].find('em').find('a').get('href'))
            soupFilmReviews = BeautifulSoup(filmReviews.text, 'html.parser')
    
            tags = soupFilmReviews.find_all('td', class_= 'text')
            for i in tags:
                if i.find('a') != None:
                    reviews.append(i.find('a').text)
                else:
                    reviews.append(i.text)
        else:
            tags = soupFilm.find_all('div', itemprop='reviewBody')
            for i in tags:
                reviews.append(i.text)
    
        reviewsComplete.append(reviews)
        reviews = []
    
    else:
        reviewsComplete.append('NaN')

https://www.filmaffinity.com/us/film879405.html
None
True 

https://www.filmaffinity.com/us/film573633.html
None
True 

https://www.filmaffinity.com/us/film441483.html
https://www.filmaffinity.com/us/film822756.html
None
True 

https://www.filmaffinity.com/us/film999360.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=999360">Show 5 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/us/film103430.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=103430">Show 4 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/us/film910593.html
None
True 

https://www.filmaffinity.com/us/film482516.html
None
True 

https://www.filmaffinity.com/us/film539830.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=539830">Show 5 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaff

https://www.filmaffinity.com/us/film846678.html
https://www.filmaffinity.com/us/film847347.html
https://www.filmaffinity.com/us/film658214.html
None
True 

https://www.filmaffinity.com/us/film900221.html
None
True 

https://www.filmaffinity.com/us/film129408.html
https://www.filmaffinity.com/us/film447173.html
None
True 

https://www.filmaffinity.com/us/film233858.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=233858">Show 24 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/us/film136730.html
https://www.filmaffinity.com/us/film417348.html
None
True 

https://www.filmaffinity.com/us/film538285.html
https://www.filmaffinity.com/us/film566155.html
None
True 

https://www.filmaffinity.com/us/film388413.html
None
True 

https://www.filmaffinity.com/us/film234251.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=234251">Show 2 more reviews <i class="fas fa-chevron-right strip-down"

None
True 

https://www.filmaffinity.com/us/film551378.html
None
True 

https://www.filmaffinity.com/us/film922716.html
None
True 

https://www.filmaffinity.com/us/film491317.html
None
True 

https://www.filmaffinity.com/us/film342360.html
None
True 

https://www.filmaffinity.com/us/film662961.html
https://www.filmaffinity.com/us/film821047.html
https://www.filmaffinity.com/us/film686560.html
None
True 

https://www.filmaffinity.com/us/film385353.html
https://www.filmaffinity.com/us/film888928.html
https://www.filmaffinity.com/us/film194361.html
https://www.filmaffinity.com/us/film586622.html
https://www.filmaffinity.com/us/film137238.html
https://www.filmaffinity.com/us/film287365.html
None
True 

https://www.filmaffinity.com/us/film736452.html
None
True 

https://www.filmaffinity.com/us/film315698.html
None
True 

https://www.filmaffinity.com/us/film384644.html
None
True 

https://www.filmaffinity.com/us/film916461.html
https://www.filmaffinity.com/us/film315845.html
https://www.film

https://www.filmaffinity.com/us/film508742.html
None
True 

https://www.filmaffinity.com/us/film289409.html
None
True 

https://www.filmaffinity.com/us/film557524.html
None
True 

https://www.filmaffinity.com/us/film851398.html
None
True 

https://www.filmaffinity.com/us/film725415.html
None
True 

https://www.filmaffinity.com/us/film636712.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=636712">Show 7 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/us/film706350.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=706350">Show 19 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/us/film189667.html
None
True 

https://www.filmaffinity.com/us/film742979.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=742979">Show 5 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https:

None
True 

https://www.filmaffinity.com/es/film619365.html
None
True 

https://www.filmaffinity.com/es/film133932.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=133932">Mostrar 7 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film190109.html
None
True 

https://www.filmaffinity.com/us/film360594.html
https://www.filmaffinity.com/us/film830168.html
<em><a href="https://www.filmaffinity.com/us/pro-reviews.php?movie-id=830168">Show 3 more reviews <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film281959.html
https://www.filmaffinity.com/us/film448330.html
None
True 

https://www.filmaffinity.com/us/film935404.html
https://www.filmaffinity.com/es/film958444.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=958444">Mostrar 7 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.

...

<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=379145">Mostrar 26 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film478053.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=478053">Mostrar 12 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film399099.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=399099">Mostrar 7 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film697877.html
None
True 

https://www.filmaffinity.com/es/film132322.html
None
True 

https://www.filmaffinity.com/es/film224989.html
None
True 

https://www.filmaffinity.com/es/film609740.html
https://www.filmaffinity.com/es/film711112.html
https://www.filmaffinity.com/es/film606078.html
None
True 

https://www.filmaffinity.com/es/film908906.html
https://www.filmaffi

<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=984792">Mostrar 35 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film701802.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=701802">Mostrar 14 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film300469.html
None
True 

https://www.filmaffinity.com/es/film623370.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=623370">Mostrar 2 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film906881.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=906881">Mostrar 3 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film218131.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=218131">Most

<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=885451">Mostrar 7 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film335668.html
None
True 

https://www.filmaffinity.com/es/film586794.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=586794">Mostrar 26 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film503855.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=503855">Mostrar 6 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film846192.html
https://www.filmaffinity.com/es/film755840.html
https://www.filmaffinity.com/es/film655136.html
https://www.filmaffinity.com/es/film967133.html
https://www.filmaffinity.com/es/film732155.html
https://www.filmaffinity.com/es/film159696.html
https://www.filmaffinity.com/es/film756425.html
https://w

https://www.filmaffinity.com/es/film785562.html
https://www.filmaffinity.com/es/film230922.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=230922">Mostrar 2 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film371085.html
None
True 

https://www.filmaffinity.com/es/film720391.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=720391">Mostrar 4 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film352786.html
https://www.filmaffinity.com/es/film232421.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=232421">Mostrar 3 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film559954.html
None
True 

https://www.filmaffinity.com/es/film402928.html
None
True 

https://www.filmaffinity.com/es/film300855.html
None
True 

https://www.filmaffini

https://www.filmaffinity.com/es/film635362.html
None
True 

https://www.filmaffinity.com/es/film993613.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=993613">Mostrar 9 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film496288.html
https://www.filmaffinity.com/es/film758857.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=758857">Mostrar 2 críticas más <i class="fas fa-chevron-right strip-down"></i></a></em>
False 

https://www.filmaffinity.com/es/film301581.html
None
True 

https://www.filmaffinity.com/es/film702709.html
None
True 

https://www.filmaffinity.com/es/film624387.html
None
True 

https://www.filmaffinity.com/es/film299957.html
None
True 

https://www.filmaffinity.com/es/film953955.html
https://www.filmaffinity.com/es/film826923.html
<em><a href="https://www.filmaffinity.com/es/pro-reviews.php?movie-id=826923">Mostrar 14 críticas más <i class="fas fa-chevron-r

In [91]:
len(reviewsComplete)

2383

In [92]:
df['Reviews'] = [', '.join(review) for review in reviewsComplete]
df.head()

Title                                             Link     Type  \
0     Money Heist  https://www.filmaffinity.com/us/film879405.html  TV show   
1   The Blacklist  https://www.filmaffinity.com/us/film573633.html  TV show   
2       Locked Up  https://www.filmaffinity.com/us/film441483.html  TV show   
3    Prison Break  https://www.filmaffinity.com/us/film822756.html  TV show   
4  13 Reasons Why  https://www.filmaffinity.com/us/film999360.html  TV show   

  Duration        Country                                          Directors  \
0  70 min.          Spain  Álex Pina, Jesús Colmenar, Miguel Ángel Vivas,...   
1  42 min.  United States  Jon Bokenkamp, Michael W. Watkins, Andrew McCa...   
2  50 min.          Spain  Iván Escobar, Esther Martínez Lobato, Daniel É...   
3  42 min.  United States  Paul Scheuring, Bobby Roth, Kevin Hooks, Dwigh...   
4  60 min.  United States  Brian Yorkey, Tom McCarthy, Kyle Patrick Alvar...   

                                                Cast  \
0  Álvaro Morte, Úrsula Corberó, Itziar Ituño, Al...   
1  James Spader, Megan Boone, Diego Klattenhoff, ...   
2  Maggie Civantos, Najwa Nimri, Roberto Enríquez...   
3  Wentworth Miller, Dominic Purcell, Robert Knep...   
4  Dylan Minnette, Katherine Langford, Christian ...   

                                              Genres  \
0  TV Series, Thriller, Mystery, Heist Film, Kidn...   
1         TV Series, Mystery, Drama, Crime, Spy Film   
2           TV Series, Thriller, Drama, Prison Drama   
3  TV Series, Action, Drama, Prison Drama, Cop Mo...   
4  TV Series, Drama, Mystery, Teen/coming-of-age,...   

                                         Description  RatingAverage    Votes  \
0  TV Series (2017-Present Day). 4 Seasons. A mys...            7.1  25691.0   
1  The world's most wanted criminal, Thomas Raymo...            6.4   5148.0   
2  Macarena Ferreiro is a young naive woman who f...            7.0   6941.0   
3  TV Series (2005-2009). 5 Seasons. 90 Episodes....            7.3  71511.0   
4  'Thirteen Reasons Why', based on the best-sell...            6.8  21496.0   

                                             Reviews  
0  "[4th Season Review]: [It] is like an extended...  
1  "His name is above the title and, depending ho...  
2                                            N, a, N  
3  "A strong cast led by Wentworth Miller (...) I...  
4  "[2nd Season Review]: [It] is a frustratingly ...

In [99]:
# Repeat the process in order to get the information from NaN values
reviews2 = []

for item in df.index:
    if df.Reviews[item] == 'NaN':
        print(df.Link[item])
        film = requests.get(df.Link[item])
        soupFilm = BeautifulSoup(film.text, 'html.parser')
        
        # reviews
        if (len(soupFilm.find_all('ul', id='pro-reviews')) != 0) == True:
        
            print(soupFilm.find_all('ul', id='pro-reviews')[0].find('em'))
            print((soupFilm.find_all('ul', id='pro-reviews')[0].find('em')) == None, '\n')
        
            if (soupFilm.find_all('ul', id='pro-reviews')[0].find('em')) != None:
                filmReviews = requests.get(soupFilm.find_all('ul', id='pro-reviews')[0].find('em').find('a').get('href'))
                soupFilmReviews = BeautifulSoup(filmReviews.text, 'html.parser')
    
                tags = soupFilmReviews.find_all('td', class_= 'text')
                for i in tags:
                    if i.find('a') != None:
                        reviews2.append(i.find('a').text)
                    else:
                        reviews2.append(i.text)
            else:
                tags = soupFilm.find_all('div', itemprop='reviewBody')
                for i in tags:
                    reviews2.append(i.text)
    
            df.Reviews[item] = ', '.join(reviews2)
            reviews2 = []
    
        else:
            df.Reviews[item] = 'NaN'

https://www.filmaffinity.com/us/film441483.html


/opt/anaconda3/envs/GinaAllWomen/lib/python3.7/site-packages/ipykernel_launcher.py:35: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


https://www.filmaffinity.com/us/film340588.html
https://www.filmaffinity.com/us/film187456.html
https://www.filmaffinity.com/us/film194842.html
https://www.filmaffinity.com/us/film880530.html
https://www.filmaffinity.com/us/film668282.html
https://www.filmaffinity.com/us/film922899.html
https://www.filmaffinity.com/us/film654192.html
https://www.filmaffinity.com/us/film871533.html
https://www.filmaffinity.com/us/film167594.html
https://www.filmaffinity.com/us/film493464.html
https://www.filmaffinity.com/us/film244225.html
https://www.filmaffinity.com/us/film462303.html
https://www.filmaffinity.com/us/film354270.html
https://www.filmaffinity.com/us/film333607.html
https://www.filmaffinity.com/us/film397789.html
https://www.filmaffinity.com/us/film332824.html
https://www.filmaffinity.com/us/film702353.html
https://www.filmaffinity.com/us/film809007.html
https://www.filmaffinity.com/us/film588857.html
https://www.filmaffinity.com/us/film730817.html
https://www.filmaffinity.com/us/film4804

https://www.filmaffinity.com/es/film913213.html
https://www.filmaffinity.com/us/film976705.html
https://www.filmaffinity.com/es/film472532.html
https://www.filmaffinity.com/us/film974286.html
https://www.filmaffinity.com/es/film399613.html
https://www.filmaffinity.com/es/film121857.html
https://www.filmaffinity.com/us/film813543.html
https://www.filmaffinity.com/es/film772178.html
https://www.filmaffinity.com/us/film830776.html
https://www.filmaffinity.com/es/film167911.html
https://www.filmaffinity.com/us/film494561.html
https://www.filmaffinity.com/us/film177512.html
https://www.filmaffinity.com/us/film339874.html
https://www.filmaffinity.com/es/film377417.html
https://www.filmaffinity.com/es/film910267.html
https://www.filmaffinity.com/es/film519962.html
https://www.filmaffinity.com/cl/film519620.html
https://www.filmaffinity.com/es/film316391.html
https://www.filmaffinity.com/es/film443074.html
https://www.filmaffinity.com/es/film985637.html
https://www.filmaffinity.com/es/film9602

https://www.filmaffinity.com/es/film241526.html
https://www.filmaffinity.com/us/film807302.html
https://www.filmaffinity.com/us/film356035.html
https://www.filmaffinity.com/es/film578892.html
https://www.filmaffinity.com/es/film764660.html
https://www.filmaffinity.com/us/film157040.html
https://www.filmaffinity.com/us/film184168.html
https://www.filmaffinity.com/es/film217074.html
https://www.filmaffinity.com/es/film559080.html
https://www.filmaffinity.com/us/film604515.html
https://www.filmaffinity.com/es/film867890.html
https://www.filmaffinity.com/es/film359286.html
https://www.filmaffinity.com/us/film553395.html
https://www.filmaffinity.com/es/film419452.html
https://www.filmaffinity.com/es/film910994.html
https://www.filmaffinity.com/es/film406717.html
https://www.filmaffinity.com/us/film160587.html
https://www.filmaffinity.com/us/film980250.html
https://www.filmaffinity.com/es/film811225.html
https://www.filmaffinity.com/es/film603154.html
https://www.filmaffinity.com/us/film6715

https://www.filmaffinity.com/es/film600324.html
https://www.filmaffinity.com/es/film160837.html
https://www.filmaffinity.com/es/film539862.html
https://www.filmaffinity.com/es/film601105.html
https://www.filmaffinity.com/es/film741902.html
https://www.filmaffinity.com/es/film619021.html
https://www.filmaffinity.com/es/film788334.html
https://www.filmaffinity.com/es/film179722.html
https://www.filmaffinity.com/es/film345773.html
https://www.filmaffinity.com/es/film814667.html
https://www.filmaffinity.com/es/film397789.html
https://www.filmaffinity.com/es/film519258.html
https://www.filmaffinity.com/es/film669621.html
https://www.filmaffinity.com/es/film747300.html
https://www.filmaffinity.com/es/film343554.html
https://www.filmaffinity.com/es/film305160.html
https://www.filmaffinity.com/es/film119391.html
https://www.filmaffinity.com/es/film916911.html
https://www.filmaffinity.com/es/film784658.html
https://www.filmaffinity.com/es/film710533.html
https://www.filmaffinity.com/es/film6603

In [100]:
# Saving the information to not lose it
df.to_csv('/Users/gina/Documents/allWomen/Final project/datasets/filmaffinity_data2.csv')